Comparar la base de datos DENUES desde el 2020 a la fecha

In [1]:
import pandas as pd
import numpy as np
import sys
'''
sys.path.append('../Funciones')  # Aacceder a la carpeta Funciones

from funciones import graficar_interactivo
from funciones import analizar_columnas
from funciones import analisis_base_dato_1'''

"\nsys.path.append('../Funciones')  # Aacceder a la carpeta Funciones\n\nfrom funciones import graficar_interactivo\nfrom funciones import analizar_columnas\nfrom funciones import analisis_base_dato_1"

In [2]:
denue_2024 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2024_11.csv", encoding='utf-8') # INEGI DENUE
denue_2020 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2020_11.csv",encoding='ISO-8859-1')
denue_2021 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2021_11.csv",encoding='ISO-8859-1')
denue_2022 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2022_11.csv",encoding='ISO-8859-1')
denue_2023 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2023_11.csv",encoding='ISO-8859-1')


# Diccionario de datos de la base de datos SCIAN, 
# Cargar y procesar SCIAN
scian = pd.read_excel("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/Diccionarios/Diccionario SCIAN.xlsx")  # Base de datos diccinario del SCIAN
scian = (
    scian[scian["Código"].astype(str).str.fullmatch(r"^\d{3}")]  # Filtrar códigos de 3 dígitos
    .assign(Título=lambda x: x["Título"].str.rstrip("T"))  # Limpiar columna "Título"
    [["Código", "Título"]]  # Seleccionar columnas
)


extendido = pd.read_excel("Extendido.xlsx") # Zona extendida
nuclear = pd.read_excel("Nuclear.xlsx") # Zona Nuclear

# Filtrar por AGEB y Manzana 
# Concatenar y filtrar zona_total_estudio
zona_total_estudio = (
    pd.concat([extendido, nuclear], ignore_index=True)  # Concatenar
    [["CVE_AGEB", "CVE_MZA"]]  # Seleccionar columnas
)

C:\Users\julio\AppData\Local\Temp\ipykernel_644\1111654487.py:1: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  denue_2024 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2024_11.csv", encoding='utf-8') # INEGI DENUE
C:\Users\julio\AppData\Local\Temp\ipykernel_644\1111654487.py:2: DtypeWarning: Columns (34) have mixed types. Specify dtype option on import or set low_memory=False.
  denue_2020 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2020_11.csv",encoding='ISO-8859-1')
C:\Users\julio\AppData\Local\Temp\ipykernel_644\1111654487.py:3: DtypeWarning: Columns (35) have mixed types. Specify dtype option on import or set low_memory=False.
  denue_2021 = pd.read_csv("C:/Users/julio/OneDrive/Documentos/Ideas Frescas/MacroDatos/DENUEs_SIN_2021_11.csv",encoding='ISO-8859-1')
C:\Users\julio\AppData\Local\Temp\ipykernel_644\1111654487.py:4: DtypeWarning: Columns 

In [3]:
denue_2024.shape[0]

124105

In [4]:
# Función para limpiar y reubicar la columna de fecha
def limpiar_fecha(df, col_fecha_original, col_fecha_nueva, posicion):
    """
    Limpia la columna de fecha y la reubica en la posición especificada.
    
    Parámetros:
        df: DataFrame a procesar.
        col_fecha_original: Nombre de la columna original de la fecha.
        col_fecha_nueva: Nombre de la nueva columna de fecha.
        posicion: Posición donde se insertará la nueva columna.
    """
    # Extraer el año de la fecha original
    df[col_fecha_nueva] = df[col_fecha_original].astype(str).str[:4]
    
    # Reubicar la nueva columna en la posición deseada
    col_f = df.pop(col_fecha_nueva)
    df.insert(posicion, col_fecha_nueva, col_f)

# Lista de DataFrames y sus respectivas columnas de fecha
dataframes = [
    (denue_2024, "fecha_alta", "Fecha de incorporación DENU", 9),
    (denue_2020, "fecha_alta", "fecha de alta", 9),
    (denue_2021, "fecha_alta", "fecha de alta", 9),
    (denue_2022, "fecha_alta", "fecha de alta", 9),
    (denue_2023, "fecha_alta", "fecha de alta", 9)
]

# Aplicar la función a cada DataFrame
for df, col_original, col_nueva, pos in dataframes:
    limpiar_fecha(df, col_original, col_nueva, pos)

In [5]:
# Agregar la principal actividad economica SCIAN a cada DENUE, basado en el diccionario que se descargo 

# Considerar solo los tres primeros digitos  del SCIAN para hacer la conección con las dos bases de datos. 
denue_2024["CLAVE SCIAN"] = denue_2024["codigo_act"].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
denue_2024 = denue_2024.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
denue_2024 = denue_2024.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a = denue_2024.pop("Principal Actividad Economica")
denue_2024.insert(2,"Principal Actividad Economica", col_a)

denue_2020["CLAVE SCIAN"] = denue_2020['codigo_act'].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
denue_2020 = denue_2020.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
denue_2020 = denue_2020.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a1 = denue_2020.pop("Principal Actividad Economica")
denue_2020.insert(2,"Principal Actividad Economica", col_a1)

denue_2021["CLAVE SCIAN"] = denue_2021['codigo_act'].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
denue_2021 = denue_2021.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
denue_2021 = denue_2021.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a2 = denue_2021.pop("Principal Actividad Economica")
denue_2021.insert(2,"Principal Actividad Economica", col_a2)

denue_2022["CLAVE SCIAN"] = denue_2022['codigo_act'].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
denue_2022 = denue_2022.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
denue_2022 = denue_2022.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a3 = denue_2022.pop("Principal Actividad Economica")
denue_2022.insert(2,"Principal Actividad Economica", col_a3)

denue_2023["CLAVE SCIAN"] = denue_2023['codigo_act'].astype(str).str[:3]
# Se unen las dos bases de datos para obtener la principal actividad economica
denue_2023 = denue_2023.merge(scian,left_on="CLAVE SCIAN", right_on="Código", how = "left")
# Se renombra la columna a utilizar
denue_2023 = denue_2023.rename(columns={"Título": "Principal Actividad Economica"})
# Posicionar la nueva columna en donde sea más facil leer la información 
col_a4 = denue_2023.pop("Principal Actividad Economica")
denue_2023.insert(2,"Principal Actividad Economica", col_a4)


In [6]:
denue_2020 = denue_2020[denue_2020["municipio"] == "Mazatlán"]
denue_2021 = denue_2021[denue_2021["municipio"] == "Mazatlán"]
denue_2022 = denue_2022[denue_2022["municipio"] == "Mazatlán"]
denue_2023 = denue_2023[denue_2023["municipio"] == "MazatlÃ¡n"]


In [7]:
# Diccionario de Variables 
'''
Diccionario de Columnas a Utilizar 
Nombre de la Unidad Económica: Es el nombre comercial o nombre exterior con el que se identifica o anuncia la unidad económica.

Código de la clase de actividad SCIAN: El código está asignado con base en la actividad principal que desarrolla la unidad económica y de acuerdo con el Sistema de Clasificación
Industrial para América del Norte.

Descripcion estrato personal ocupado: Permite identificar el tamaño de Unidades Económicas por el número
de personal que emplean.

Tipo de vialidad: Es la superficie del terreno destinada para el tránsito vehicular y/o peatonal, en la cual se encuentra ubicada la unidad económica (calle, avenida,
andado.

Tipo de asentamiento humano: Es la clasificación que se da al asentamiento humano de acuerdo con su función (colonia, fraccionamiento, unidad habitacional, etc.).

Nombre de asentamiento humano:Es el sustantivo propio con el cual se identifica el asentamiento humano.

Tipo centro comercial: Son los caracteres alfanuméricos con los que se identifica el tipo de plaza, centro comercial, mercado.

Tipo de establecimiento: En este tipo de establecimiento están comprendidas las viviendas cuando en algún espacio de la casa-habitación, que también está destinado a
otras actividades cotidianas, se realiza alguna actividad económica.

Fecha de incorporación al DENUE: Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Área geoestadística básica: Marco Geoestadístico Naciona.

Manzana: xtensión territorial que está constituida por un grupo de
viviendas, edificios, predios, lotes o terrenos de uso habitacional, comercial, industrial o de servicios.

Latitud: Es la distancia que existe entre la unidad económica y el ecuador. 

Fecha en la que la unidad económica se integró al Directorio Estadístico Nacional de Unidades Económicas.

Longitud: Es la distancia que existe entre la unidad económica y el meridiano de Greenwich.-

'''

# Lista de variables a considerar y filtrado por esas columnas 

denue_2024 = denue_2024[['nom_estab', 
                'Principal Actividad Economica', 
                'per_ocu',
                'tipo_vial',
                'tipo_asent',
                'nomb_asent', 
                'tipoCenCom',
                'nom_CenCom',
                'fecha_alta',
                'ageb', 
                'manzana',
                'latitud',
                'longitud',
                         ]]

lista_filtro = ['nom_estab', 
                'Principal Actividad Economica', 
                'per_ocu',
                'tipo_vial',
                'tipo_asent',
                'nomb_asent', 
                'tipoCenCom',
                'nom_CenCom',
                'fecha de alta',
                'ageb', 
                'manzana',
                'latitud',
                'longitud',
                         ]


denue_2020 = denue_2020[lista_filtro]
denue_2021 = denue_2021[lista_filtro]
denue_2022 = denue_2022[lista_filtro]
denue_2023 = denue_2023[lista_filtro]


In [8]:
denue_2024

nom_estab  \
0                                     TORTILLERIA CHHERRY   
1                                      TORTILLERÍA CHELYS   
2                                  TORTILLERIA CHINOBAMPO   
3                                      TORTILLERIA CHICHI   
4                                     TORTILLERIA CHELITO   
...                                                   ...   
124100                 SINDICATURA MUNICIPAL LEON FONSECA   
124101                          SINDICATURA RUIZ CORTINES   
124102                               BODEGA DIF. ZONA SUR   
124103  SINDICATURA MUNICIPAL DE VILLA LICENCIADO ADOL...   
124104                   SINDICATURA MUNICIPAL EL BURRION   

                            Principal Actividad Economica           per_ocu  \
0                                   Industria alimentaria    0 a 5 personas   
1                                   Industria alimentaria    0 a 5 personas   
2                                   Industria alimentaria   6 a 10 personas   
3                                   Industria alimentaria    0 a 5 personas   
4                                   Industria alimentaria    0 a 5 personas   
...                                                   ...               ...   
124100  Actividades legislativas, gubernamentales y de...  11 a 30 personas   
124101  Actividades legislativas, gubernamentales y de...  11 a 30 personas   
124102  Actividades legislativas, gubernamentales y de...    0 a 5 personas   
124103  Actividades legislativas, gubernamentales y de...  11 a 30 personas   
124104  Actividades legislativas, gubernamentales y de...   6 a 10 personas   

        tipo_vial       tipo_asent                  nomb_asent tipoCenCom  \
0           CALLE          COLONIA                      CENTRO        NaN   
1           CALLE            EJIDO             RINCON DE URIAS        NaN   
2           CALLE        LOCALIDAD          LIC. BENITO JUAREZ        NaN   
3       BOULEVARD           CIUDAD              JUAN JOSE RIOS        NaN   
4           CALLE  FRACCIONAMIENTO               VALLE DEL SOL        NaN   
...           ...              ...                         ...        ...   
124100      CALLE        LOCALIDAD                LEON FONSECA        NaN   
124101      CALLE        LOCALIDAD        ADOLFO RUIZ CORTINES        NaN   
124102    AVENIDA          COLONIA                      CENTRO        NaN   
124103    AVENIDA        LOCALIDAD  PUEBLO ADOLFO LOPEZ MATEOS        NaN   
124104    AVENIDA        LOCALIDAD                  EL BURRION        NaN   

       nom_CenCom fecha_alta  ageb  manzana    latitud    longitud  
0             NaN    2019-11  1330        5  25.947530 -109.047476  
1             NaN    2019-11  1885       26  23.236945 -106.387523  
2             NaN    2010-07  1430       17  25.661973 -108.619204  
3             NaN    2010-07  1464       27  25.751189 -108.824682  
4             NaN    2021-11  3148       13  23.256312 -106.374987  
...           ...        ...   ...      ...        ...         ...  
124100        NaN    2010-07  0235        1  25.733416 -108.343587  
124101        NaN    2010-07  0201       32  25.704476 -108.718194  
124102        NaN    2014-12  067A        5  22.838311 -105.774435  
124103        NaN    2010-07  2212       13  24.896407 -107.631587  
124104        NaN    2011-03  1318       10  25.540466 -108.408529  

[124105 rows x 13 columns]

In [9]:
#Base de datos de DENUE filtrado por el AGEB y Manzanas por los poligonos trazados para el area de estudio para conocer la zona. 
denue_2020 = denue_2020.merge(zona_total_estudio,left_on=["ageb", "manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})
denue_2021 = denue_2021.merge(zona_total_estudio,left_on=["ageb", "manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})
denue_2022 = denue_2022.merge(zona_total_estudio,left_on=["ageb", "manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})
denue_2023 = denue_2023.merge(zona_total_estudio,left_on=["ageb", "manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})
denue_2024 = denue_2024.merge(zona_total_estudio,left_on=["ageb", "manzana"],right_on=["CVE_AGEB","CVE_MZA"]).replace({'*': '0', np.nan: "DESCONOCIDO"})

In [10]:
denue_2024

nom_estab  \
0                                TORTILLERIA DAVID   
1                         PURIFICADORA FUENTE SANA   
2                      TORTILLERIA DE HARINA ANITA   
3                         PURIFICADORA LA SIRENITA   
4                                  TORTILLERIA LUZ   
...                                            ...   
1609       TALLERES NAVALES E INDUSTRIALES PACHECO   
1610                             SEMARNAT Y CREDES   
1611   CASETA DE POLICIA MUNICIPAL BONFIL MAZATLÁN   
1612                  CAMPAMENTO DE OBRAS PUBLICAS   
1613  BODEGA MUNICIPAL DE ARCHIVO DE CONCENTRACIÓN   

                          Principal Actividad Economica             per_ocu  \
0                                 Industria alimentaria      0 a 5 personas   
1                 Industria de las bebidas y del tabaco      0 a 5 personas   
2                                 Industria alimentaria      0 a 5 personas   
3                 Industria de las bebidas y del tabaco      0 a 5 personas   
4                                 Industria alimentaria      0 a 5 personas   
...                                                 ...                 ...   
1609            Servicios de reparación y mantenimiento    11 a 30 personas   
1610  Actividades legislativas, gubernamentales y de...    11 a 30 personas   
1611  Actividades legislativas, gubernamentales y de...    11 a 30 personas   
1612  Actividades legislativas, gubernamentales y de...  101 a 250 personas   
1613  Actividades legislativas, gubernamentales y de...      0 a 5 personas   

     tipo_vial         tipo_asent        nomb_asent         tipoCenCom  \
0        CALLE            COLONIA     GABRIEL LEYVA        DESCONOCIDO   
1      AVENIDA            COLONIA          MONTUOSA        DESCONOCIDO   
2        CALLE            COLONIA           SHIMIZU        DESCONOCIDO   
3        CALLE            COLONIA          MONTUOSA        DESCONOCIDO   
4        CALLE            COLONIA           MONTUOA        DESCONOCIDO   
...        ...                ...               ...                ...   
1609     CALLE            COLONIA      CASA REDONDA        DESCONOCIDO   
1610   AVENIDA  PARQUE INDUSTRIAL  ALFREDO V BONFIL  PARQUE INDUSTRIAL   
1611   AVENIDA            COLONIA      CASA REDONDA        DESCONOCIDO   
1612   AVENIDA            COLONIA      CASA REDONDA        DESCONOCIDO   
1613     CALLE            COLONIA            CENTRO        DESCONOCIDO   

                              nom_CenCom fecha_alta  ageb  manzana    latitud  \
0                            DESCONOCIDO    2019-11  0374       31  23.202852   
1                            DESCONOCIDO    2012-06  0336       35  23.209546   
2                            DESCONOCIDO    2019-11  0336        6  23.213588   
3                            DESCONOCIDO    2010-07  0336       10  23.209529   
4                            DESCONOCIDO    2010-07  0340       16  23.211172   
...                                  ...        ...   ...      ...        ...   
1609                         DESCONOCIDO    2010-07  1669       15  23.216199   
1610  PARQUE INDUSTRIAL ALFREDO V BONFIL    2010-07  1654       28  23.213779   
1611                         DESCONOCIDO    2014-12  1654       30  23.216627   
1612                         DESCONOCIDO    2010-07  1669        1  23.215380   
1613                         DESCONOCIDO    2014-12  0321       39  23.205065   

        longitud CVE_AGEB  CVE_MZA  
0    -106.413566     0374       31  
1    -106.415862     0336       35  
2    -106.414208     0336        6  
3    -106.412320     0336       10  
4    -106.412576     0340       16  
...          ...      ...      ...  
1609 -106.402416     1669       15  
1610 -106.402271     1654       28  
1611 -106.403409     1654       30  
1612 -106.398055     1669        1  
1613 -106.418720     0321       39  

[1614 rows x 15 columns]

In [12]:
df_actividades = denue_2024["Principal Actividad Economica"].value_counts().reset_index()
df_actividades.columns = ["Actividad Economica", "Cantidad"]
df_actividades

Actividad Economica  Cantidad
0   Comercio al por menor de abarrotes, alimentos,...       210
1             Servicios de reparación y mantenimiento       199
2     Servicios de preparación de alimentos y bebidas       195
3                               Pesca, caza y captura       128
4                                Servicios personales        84
5                               Industria alimentaria        60
6   Servicios médicos de consulta externa y servic...        51
7   Comercio al por menor de artículos de ferreter...        46
8   Comercio al por menor de enseres domésticos, c...        43
9   Comercio al por mayor de materias primas agrop...        43
10                 Fabricación de productos metálicos        40
11    Servicios profesionales, científicos y técnicos        38
12                      Asociaciones y organizaciones        38
13  Comercio al por menor de artículos de papelerí...        33
14  Comercio al por menor de vehículos de motor, r...        29
15  Comercio al por mayor de maquinaria, equipo y ...        28
16                               Servicios educativos        26
17  Actividades legislativas, gubernamentales y de...        22
18                  Servicios de apoyo a los negocios        22
19  Comercio al por mayor de abarrotes, alimentos,...        22
20  Comercio al por menor en tiendas de autoservic...        17
21               Otros servicios de asistencia social        16
22                     Impresión e industrias conexas        16
23              Industria de las bebidas y del tabaco        16
24                             Industria de la madera        15
25  Comercio al por menor de artículos para el cui...        15
26  Comercio al por menor de productos textiles, b...        14
27  Instituciones de intermediación crediticia y f...        14
28                   Fabricación de prendas de vestir        13
29  Fabricación de productos textiles, excepto pre...        11
30      Fabricación de muebles, colchones y persianas         8
31  Servicios de entretenimiento en instalaciones ...         8
32                            Servicios inmobiliarios         8
33                  Servicios de alojamiento temporal         7
34           Servicios relacionados con el transporte         7
35  Generación, transmisión, distribución y comerc...         7
36  Comercio al por mayor de productos farmacéutic...         6
37                            Autotransporte de carga         6
38            Servicios de alquiler de bienes muebles         6
39  Servicios artísticos, culturales y deportivos,...         6
40                 Fabricación de maquinaria y equipo         5
41                    Otras industrias manufactureras         5
42  Residencias de asistencia social y para el cui...         3
43  Transporte terrestre de pasajeros, excepto por...         3
44                     Cría y explotación de animales         3
45       Trabajos especializados para la construcción         3
46                Fabricación de equipo de transporte         2
47  Curtido y acabado de cuero y piel, y fabricaci...         2
48                  Industria del plástico y del hule         2
49  Fabricación de productos a base de minerales n...         2
50                                 Telecomunicaciones         2
51                        Servicios de almacenamiento         2
52               Servicios de mensajería y paquetería         2
53                                  Industria química         1
54                                Industria del papel         1
55  Comercio al por mayor de camiones y de partes ...         1
56  Dirección y administración de grupos empresari...         1
57                                Transporte por agua         1

In [13]:
# Crear el CSV de la base de datos filtrados 
df_actividades.to_csv("Actividades Economicas SCIAN 2024.csv", index=False, encoding='ISO-8859-1')

In [ ]:
denues_en_2020 = denue_2020.shape[0]
denues_en_2021 = denue_2021.shape[0]
denues_en_2022 = denue_2022.shape[0]
denues_en_2023 = denue_2023.shape[0]
denues_en_2024 = denue_2024.shape[0]

In [ ]:
# Obtener las actividades económicas y sus conteos
actividades_2020 = denue_2020["Principal Actividad Economica"].value_counts()

# Crear listas para almacenar las actividades y sus conteos
actividades = actividades_2020.index.tolist()  # Nombres de las actividades
conteos = actividades_2020.values.tolist()     # Número de ocurrencias

# Crear la lista final con los resultados
lista_2020 = [denues_en_2020]  # Agregar el valor de `denues_en_2020`

# Agregar las actividades y sus conteos a la lista
for i in range(6):  # Solo las primeras 6 actividades
    lista_2020.extend([actividades[i], conteos[i]])

# Si hay menos de 6 actividades, rellenar con "N/A" y 0
while len(lista_2020) < 13:  # 1 (denues_en_2020) + 6 actividades * 2 (nombre y conteo)
    lista_2020.extend(["N/A", 0])



# Obtener las actividades económicas y sus conteos
actividades_2021 = denue_2021["Principal Actividad Economica"].value_counts()

# Crear listas para almacenar las actividades y sus conteos
actividades_1 = actividades_2021.index.tolist()  # Nombres de las actividades
conteos_1 = actividades_2021.values.tolist()     # Número de ocurrencias

# Crear la lista final con los resultados
lista_2021 = [denues_en_2021]  # Agregar el valor de `denues_en_2021`

# Agregar las actividades y sus conteos a la lista
for i in range(6):  # Solo las primeras 6 actividades
    lista_2021.extend([actividades_1[i], conteos_1[i]])

# Si hay menos de 6 actividades, rellenar con "N/A" y 0
while len(lista_2021) < 13:  # 1 (denues_en_2021) + 6 actividades * 2 (nombre y conteo)
    lista_2021.extend(["N/A", 0])



# Obtener las actividades económicas y sus conteos
actividades_2022 = denue_2022["Principal Actividad Economica"].value_counts()

# Crear listas para almacenar las actividades y sus conteos
actividades_2 = actividades_2022.index.tolist()  # Nombres de las actividades
conteos_2 = actividades_2022.values.tolist()     # Número de ocurrencias

# Crear la lista final con los resultados
lista_2022 = [denues_en_2022]  # Agregar el valor de `denues_en_2022`

# Agregar las actividades y sus conteos a la lista
for i in range(6):  # Solo las primeras 6 actividades
    lista_2022.extend([actividades_2[i], conteos_2[i]])

# Si hay menos de 6 actividades, rellenar con "N/A" y 0
while len(lista_2022) < 13:  # 1 (denues_en_2022) + 6 actividades * 2 (nombre y conteo)
    lista_2022.extend(["N/A", 0])


# Obtener las actividades económicas y sus conteos
actividades_2023 = denue_2023["Principal Actividad Economica"].value_counts()

# Crear listas para almacenar las actividades y sus conteos
actividades_3 = actividades_2023.index.tolist()  # Nombres de las actividades
conteos_3 = actividades_2023.values.tolist()     # Número de ocurrencias

# Crear la lista final con los resultados
lista_2023 = [denues_en_2023]  # Agregar el valor de `denues_en_2023`

# Agregar las actividades y sus conteos a la lista
for i in range(6):  # Solo las primeras 6 actividades
    lista_2023.extend([actividades_3[i], conteos_3[i]])

# Si hay menos de 6 actividades, rellenar con "N/A" y 0
while len(lista_2023) < 13:  # 1 (denues_en_2023) + 6 actividades * 2 (nombre y conteo)
    lista_2023.extend(["N/A", 0])


# Obtener las actividades económicas y sus conteos
actividades_2024 = denue_2024["Principal Actividad Economica"].value_counts()

# Crear listas para almacenar las actividades y sus conteos
actividades_4 = actividades_2024.index.tolist()  # Nombres de las actividades
conteos_4 = actividades_2024.values.tolist()     # Número de ocurrencias

# Crear la lista final con los resultados
lista_2024 = [denues_en_2024]  # Agregar el valor de `denues_en_2024`

# Agregar las actividades y sus conteos a la lista
for i in range(6):  # Solo las primeras 6 actividades
    lista_2024.extend([actividades_4[i], conteos_4[i]])

# Si hay menos de 6 actividades, rellenar con "N/A" y 0
while len(lista_2024) < 13:  # 1 (denues_en_2024) + 6 actividades * 2 (nombre y conteo)
    lista_2024.extend(["N/A", 0])


In [ ]:
# Crear el DataFrame comparativo
comparativo = pd.DataFrame({
    'Descripción': [
        'Total de Denues',
        'Principal actividad', 
        'Total DENUES de la principal actividad',
        'Segunda actividad',
        'Total DENUES de la segunda actividad',
        'Tercera actividad',
        'Total DENUES de la tercera actividad',
        'Cuarta Actividad',
        'Total DENUES de la cuarta actividad',
        'Quinta Actividad',
        'Total DENUES de la quinta actividad',
        'Sexta Actividad',
        'Total DENUES de la Sexta actividad'
    ]
})

# Diccionario con las listas de cada año
listas_por_anio = {
    '2020': lista_2020,
    '2021': lista_2021,
    '2022': lista_2022,
    '2023': lista_2023,
    '2024': lista_2024
}

# Asignar las listas a las columnas correspondientes
for anio, lista in listas_por_anio.items():
    comparativo[anio] = lista

In [ ]:
comparativo

In [ ]:
# Crear el CSV de la base de datos filtrados 
#comparativo.to_csv("Comparativo DENUES historicos Mazatlán.csv", index=False, encoding='ISO-8859-1')

In [ ]:
registros_totales_2020, x =denue_2020[denue_2020["Principal Actividad Economica"]=='Pesca, caza y captura'].shape
registros_totales_2021, x =denue_2021[denue_2021["Principal Actividad Economica"]=='Pesca, caza y captura'].shape
registros_totales_2022, x =denue_2022[denue_2022["Principal Actividad Economica"]=='Pesca, caza y captura'].shape
registros_totales_2023, x =denue_2023[denue_2023["Principal Actividad Economica"]=='Pesca, caza y captura'].shape
registros_totales_2024, x =denue_2024[denue_2024["Principal Actividad Economica"]=='Pesca, caza y captura'].shape

In [ ]:
import pandas as pd

# Crear un diccionario con los años y sus respectivos valores
datos_pesca = {
    "Año": [2020, 2021, 2022, 2023, 2024],
    "Registros Totales": [
        registros_totales_2020, 
        registros_totales_2021, 
        registros_totales_2022, 
        registros_totales_2023, 
        registros_totales_2024
    ]
}

# Convertir el diccionario en un DataFrame
df_pesca = pd.DataFrame(datos_pesca)

# Mostrar el DataFrame
df_pesca


Analizar el Parque Bonfirl en la zona de estudio 

In [ ]:
lista_zona_nautica = denue_2024["Nombre de asentamiento humano"].unique().tolist()
colonias = [1,13,17,18,30,36,39,40,41,46,52,67,68,69,71,75]
lista_zona_nautica = [lista_zona_nautica[i] for i in colonias]
zona_nautica = denue_2024[denue_2024["Nombre de asentamiento humano"].isin(lista_zona_nautica)]
zona_nautica.head(5)

In [ ]:
lista_zona_nautica

In [ ]:
principal_actividad_nautica = analizar_columnas(zona_nautica,"Principal Actividad Economica",100)
principal_actividad_nautica.head(4)

# Crear el CSV de la base de datos filtrados 
#principal_actividad_nautica.to_csv("Principal actividad economica en la zona nautica.csv", index=False, encoding='ISO-8859-1')

In [ ]:
personal_ocupado_nautica = analizar_columnas(zona_nautica,"Descripcion estrato personal ocupado",100)
personal_ocupado_nautica.head(8)

# Crear el CSV de la base de datos filtrados 
#personal_ocupado_nautica.to_csv("Descripcion estrato personal ocupado en la zona nautica.csv", index=False, encoding='ISO-8859-1')

Ahora analizaremos a más profundidad las empresas de 51 empleados y más en el parque bonfil 

In [ ]:
personal_ocupado = ["51 a 100 personas",'101 a 250 personas','251 y más persona']
zona_nautica__empresasgrandes = zona_nautica[zona_nautica['Descripcion estrato personal ocupado'].isin(personal_ocupado)]
zona_nautica__empresasgrandes.head(5)

In [ ]:
empresas_grandes_nautica = analizar_columnas(zona_nautica__empresasgrandes,"Principal Actividad Economica",100)
empresas_grandes_nautica.head(10)
# Crear el CSV de la base de datos filtrados 
#empresas_grandes_nautica.to_csv("Principal actividad economica empresas con 51 empleado o más en la zona nautica.csv", index=False, encoding='ISO-8859-1')

In [ ]:
listado_empresas_zona_nautica = zona_nautica__empresasgrandes[['Nombre de la Unidad Económica','Fecha de incorporación DENU','Latitud','Longitud']]
listado_empresas_zona_nautica.head(5)
# Crear el CSV de la base de datos filtrados 
#listado_empresas_zona_nautica.to_csv("Listado de las empresas a considerar en la zona nautica.csv", index=False, encoding='ISO-8859-1')